In [1]:
import igraph
import community
import pandas as pd
import matplotlib.pyplot as plt
import numpy as np
import math
import matplotlib.patches as mpatches
import matplotlib.pyplot as plt
import os
import pygraphviz
os.chdir("../src")
from build_network_object import build_network_object
from draw_network_by_classification import draw_network_by_classification, compare_degrees_strength
from draw_adjacency_matrix import draw_adjacency_matrix
from draw_and_print_communities import draw_and_print_communities, compare_comunity_intersection
from correlations import correlation_industry_pairs, correlation_network_degree,correlation_adjacency_matrix
from networkx_functions import build_networx_network, build_networx_from_df, include_mstree_information, prepare_dataframe_for_gephi
import seaborn as sns
import networkx as nx

# Data processing for Gephi:

Gephi can be difficult to use, and implies lots of 'clicking' which reduces the posibility to reproduce the results. In here we process the data to avoid the use of Gephi in the algorithmic steps of building a backbone tree for the visualisation (maximum spanning tree), the we transform the data into the shape espected for Gephi. 

In [2]:
# Read the data exported from the secure lab
label1 = "Table1_Reduced_matrix_2009_2018_flows"
reduced_matrix_2009_2018 = pd.read_csv("../data/"+label1+".csv", index_col=0)

reduced_matrix_2009_2018_flows = reduced_matrix_2009_2018[reduced_matrix_2009_2018['StartIndst']!=0]

# delete self loops
sub_matrix_2009_2018_flows = reduced_matrix_2009_2018_flows[reduced_matrix_2009_2018_flows['weight']<1].sort_values(by=['weight'], ascending=False)
sub_matrix_2009_2018_flows = sub_matrix_2009_2018_flows[sub_matrix_2009_2018_flows['weight']>0].sort_values(by=['weight'], ascending=False)

print ("Number of links:", sub_matrix_2009_2018_flows.shape[0]/2)
print ("Number of 4-digit industries observed:")
print (len(np.unique([sub_matrix_2009_2018_flows['StartIndst'].values,sub_matrix_2009_2018_flows['FinalIndst'].values])))
sub_matrix_2009_2018_flows[1:15]

Number of links: 1153.0
Number of 4-digit industries observed:
356


StartIndst  FinalIndst    weight             SubActivity_StartIndst  \
4321        4611        4623  0.999931    Agriculture, animals, raw goods   
4297        2732        2731  0.999828   Other electronic, electric wires   
4229        2731        2732  0.999821                 Fibre optic cables   
4191        1813        1712  0.999697      Pre-press, pre-media services   
4141        1712        1813  0.999649                  Paper, paperboard   
3986        3040        3311  0.999642         Military fighting vehicles   
4174        2899        2620  0.999599                              Other   
4226        2620        2899  0.999597    Computers, peripheral equipment   
4291        2312        2311  0.999567     Flat glass shaping, processing   
4324        3311        3040  0.999539          Fabricated metal products   
3962        2311        2312  0.999526             Flat glass manufacture   
4210         812        2362  0.999505   Gravel, sand pits; clays, kaolin   
4187        2362         812  0.999501  Plaster products for construction   
4155        2814        2812  0.999479                 Other taps, valves   

                 SubActivity_FinalIndst              MainActivity_StartIndst  \
4321                       Live animals             Fee/contract - wholesale   
4297                 Fibre optic cables                 Electrical equipment   
4229   Other electronic, electric wires                 Electrical equipment   
4191                  Paper, paperboard                             Printing   
4141      Pre-press, pre-media services             Paper and paper products   
3986          Fabricated metal products            Other transport equipment   
4174    Computers, peripheral equipment            Special purpose machinery   
4226                              Other        Computer, electronic, optical   
4291             Flat glass manufacture                       Glass products   
4324         Military fighting vehicles  Repair/installation excl. household   
3962     Flat glass shaping, processing                       Glass products   
4210  Plaster products for construction          Mining, Quarrying and other   
4187   Gravel, sand pits; clays, kaolin         Concrete, cement and plaster   
4155              Fluid power equipment                    General machinery   

                  MainActivity_FinalIndst  \
4321               Agricultural wholesale   
4297                 Electrical equipment   
4229                 Electrical equipment   
4191             Paper and paper products   
4141                             Printing   
3986  Repair/installation excl. household   
4174        Computer, electronic, optical   
4226            Special purpose machinery   
4291                       Glass products   
4324            Other transport equipment   
3962                       Glass products   
4210         Concrete, cement and plaster   
4187          Mining, Quarrying and other   
4155                    General machinery   

                                MainIndustry_StartIndst  \
4321  Wholesale and retail,motor vehicle repair,sale...   
4297  Manufacture computer, electronic, light electr...   
4229  Manufacture computer, electronic, light electr...   
4191                            All other Manufacturing   
4141                            All other Manufacturing   
3986          Manufacture machinery, vehicle, transport   
4174          Manufacture machinery, vehicle, transport   
4226  Manufacture computer, electronic, light electr...   
4291                            All other Manufacturing   
4324          Machinery repair excluding motor vehicles   
3962                            All other Manufacturing   
4210  Mining, Quarrying (inc extraction of petroleum...   
4187                            All other Manufacturing   
4155          Manufacture machinery, vehicle, transport   

                                MainIndustry_FinalIndst  Counts  
4321  Wholesale and r

In [3]:
# Read the data exported from the secure lab
label1 = "Table2_Reduced_matrix_2009_2018_connections"
reduced_matrix_2009_2018_conn = pd.read_csv("../data/"+label1+".csv", index_col=0)

reduced_matrix_2009_2018_conn = reduced_matrix_2009_2018_conn[reduced_matrix_2009_2018_conn['StartIndst']!=0]

# delete self loops
sub_matrix_2009_2018_conns = reduced_matrix_2009_2018_conn[reduced_matrix_2009_2018_conn['weight']<1].sort_values(by=['weight'], ascending=False)
sub_matrix_2009_2018_conns = reduced_matrix_2009_2018_conn[reduced_matrix_2009_2018_conn['weight']>0].sort_values(by=['weight'], ascending=False)

print ("Number of links:", reduced_matrix_2009_2018_conn.shape[0]/2)
print ("Number of 4-digit industries observed:")
print (len(np.unique([sub_matrix_2009_2018_conns['StartIndst'].values,sub_matrix_2009_2018_conns['FinalIndst'].values])))
sub_matrix_2009_2018_conns[1:15]

Number of links: 2570.5
Number of 4-digit industries observed:
445


StartIndst  FinalIndst  weight            SubActivity_StartIndst  \
4257        3521        3521     1.0                   Gas manufacture   
4170        8129        8129     1.0         Other cleaning activities   
4176        8130        8130     1.0      Landscape service activities   
4181        4329        4329     1.0   Other construction installation   
4188        4532        4532     1.0   Retail trade parts, accessories   
4192        1082        1082     1.0  Cocoa, choc, sugar confectionery   
4206        4110        4110     1.0     Building projects development   
4212        1089        1089     1.0           Other food products nec   
4221        4671        4671     1.0           Fuels, related products   
4236        9313        9313     1.0                Fitness facilities   
4241        9412        9412     1.0                      Professional   
4250        2511        2511     1.0        Metal structures, parts of   
4270        8510        8510     1.0                       Pre-primary   
4612        4942        4942     1.0                  Removal services   

                SubActivity_FinalIndst              MainActivity_StartIndst  \
4257                   Gas manufacture     Electricity, gas, steam, air con   
4170         Other cleaning activities      Buildings, landscape activities   
4176      Landscape service activities      Buildings, landscape activities   
4181   Other construction installation               Specialised activities   
4188   Retail trade parts, accessories    Motor vehicle/cycle trade, repair   
4192  Cocoa, choc, sugar confectionery                Food products - other   
4206     Building projects development            Construction of buildings   
4212           Other food products nec                Food products - other   
4221           Fuels, related products                      Other wholesale   
4236                Fitness facilities     Sports activities and recreation   
4241                      Professional  Membership organisations activities   
4250        Metal structures, parts of      Other fabricated metal products   
4270                       Pre-primary                            Education   
4612                  Removal services             Land, pipeline transport   

                  MainActivity_FinalIndst  \
4257     Electricity, gas, steam, air con   
4170      Buildings, landscape activities   
4176      Buildings, landscape activities   
4181               Specialised activities   
4188    Motor vehicle/cycle trade, repair   
4192                Food products - other   
4206            Construction of buildings   
4212                Food products - other   
4221                      Other wholesale   
4236     Sports activities and recreation   
4241  Membership organisations activities   
4250      Other fabricated metal products   
4270                            Education   
4612             Land, pipeline transport   

                                MainIndustry_StartIndst  \
4257           Utilities, sewerage, waste and recycling   
4170                                  Business services   
4176                                  Business services   
4181  Construction (including development of real es...   
4188  Wholesale and retail,motor vehicle repair,sale...   
4192                   Manufacture food, drink, tobacco   
4206  Construction (including development of real es...   
4212                   Manufacture food, drink, tobacco   
4221  Wholesale and retail,motor vehicle repair,sale...   
4236                           Other Service activities   
4241                           Other Service activities   
4250                            All other Manufacturing   
4270  Government administrative functions, Education...   
4612                         Transportation and Storage   

                                MainIndustry_FinalIndst  Counts  
4257           Utilities, sewerage, waste and recycling    52.0  
4170           

In [4]:
ad, indx = draw_adjacency_matrix(reduced_matrix_2009_2018,['StartIndst','FinalIndst'],'weight')

In [ ]:
# build network from the dataframe
network_largest_2009_2018_nx= build_networx_from_df(sub_matrix_2009_2018_flows)

partition = community.best_partition(network_largest_2009_2018_nx)

print (community.modularity(partition, network_largest_2009_2018_nx))

partition_df = pd.DataFrame.from_dict(partition,orient='index',columns=['Comunity'])
partition_df['SIC2007'] = partition_df.index

partition_df.head()

In [ ]:
label_bres = "Bres_2015_Region_and_Country"
industry_size = pd.read_csv("../data/"+label_bres+".csv", index_col=0)

industry_size.astype({'SIC2007': 'int'}).dtypes
industry_size.head(-1) 


In [ ]:
result_size = pd.merge(industry_size,partition_df,on=['SIC2007'],how='inner')

result_size.head()

In [ ]:
# Read the data exported from the secure lab
label1 = "sic-industry-structure"
industry_structure = pd.read_csv("../data/"+label1+".csv")

result_all = pd.merge(result_size,industry_structure,on=['SIC2007'],how='inner')

result_all['Id'] = result_all['SIC2007']

result_all = result_all.drop(columns="SIC2007")

result_all.to_csv("../data/ForGephi/"+label1+"-size_forGephi.csv", index=False)

result_all.head()

In [ ]:

#apply Maximum spannign tree
network_largest_2008_2018_max_span_tree = nx.maximum_spanning_tree(network_largest_2009_2018_nx)
# get edges existing in the mst
edges_list = list(network_largest_2008_2018_max_span_tree.edges())

In [ ]:
# include the mstree information back into the 
#original dataframe (there will be a new label with the information if the edges exist in the mst or not)
matrix_2009_2018_flows_with_mst = include_mstree_information(sub_matrix_2009_2018_flows,edges_list,0.5)

matrix_2009_2018_flows_with_mst.head()

In [ ]:
# transform the data into the style needed for Gephi
output_gephi = prepare_dataframe_for_gephi(matrix_2009_2018_flows_with_mst,True)

output_gephi.head()

In [ ]:
output_gephi.to_csv("../data/ForGephi/"+label1+"_Gephi.csv")

In [ ]:
output_gephi.shape